<a href="https://colab.research.google.com/github/Jfernando0120/TALLERES-SyS/blob/main/transformadal.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>



1. Descargue 10 segundos de la canción de su preferencia desde youtube, y generé un filtro pasabanda (el usuario debe poder definir las frecuencias de corte) para cada uno de los filtros descritos (el usuario también debe poder fijar los parámetros de diseño de cada filtro). Compare los resultados de los filtros estudiados en este cuaderno tipo IIR para diseño Butterworth, Chebyshev 1, Chebyshev 2, Bessel y Elíptico.

2. Consulte en qué consiste el método de diseño de filtros FIR por ventaneo (Ver función [firwin](https://docs.scipy.org/doc/scipy/reference/generated/scipy.signal.firwin.html) y [material de apoyo](https://ccrma.stanford.edu/~jos/sasp/Window_Method_FIR_Filter.html#:~:text=The%20window%20method%20for%20digital,and%20windows%20for%20spectrum%20analysis)). Realice un cuadro comparativo de las ventajas y desventajas de los filtros IIR y los FIR.

3. Incluya la implementación del filtro `firwin` en el punto 1.


In [ ]:
#LIBRERIAS
from IPython.display import Markdown as md
import soundfile as sf
from IPython.display import Audio
from scipy.signal import butter
from scipy.signal import lfilter, filtfilt

import numpy as np
from matplotlib import pyplot as plt
from matplotlib.patches import Circle
from scipy.signal import freqz_zpk

!python3 -m pip install --force-reinstall https://github.com/yt-dlp/yt-dlp/archive/master.tar.gz

link="https://www.youtube.com/watch?v=rUuusqy50yk"
!yt-dlp --extract-audio -o "audio" --audio-format mp3 {link}
!ffmpeg -y -i audio.mp3 output.wav
!pip install soundfile
import soundfile as sf # para instalar pip install soundfile
#lee archivos wav
nombre_out = "output.wav"
x, fs = sf.read(nombre_out)
# read speech signal from file
print('Frecuencia de muestreo %.2f[Hz]\naudio %s' % (fs,nombre_out))




  Using cached https://github.com/yt-dlp/yt-dlp/archive/master.tar.gz (2.6 MB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
  Using cached mutagen-1.47.0-py3-none-any.whl (194 kB)
  Using cached pycryptodomex-3.19.0-cp35-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (2.1 MB)
  Using cached websockets-12.0-cp310-cp310-manylinux_2_5_x86_64.manylinux1_x86_64.manylinux_2_17_x86_64.manylinux2014_x86_64.whl (130 kB)
  Using cached certifi-2023.11.17-py3-none-any.whl (162 kB)
  Using cached requests-2.31.0-py3-none-any.whl (62 kB)
  Using cached urllib3-2.1.0-py3-none-any.whl (104 kB)
  Using cached Brotli-1.1.0-cp310-cp310-manylinux_2_5_x86_64.manylinux1_x86_64.manylinux_2_12_x86_64.manylinux2010_x86_64.whl (3.0 MB)
  Using cached charset_normalizer-3.3.2-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (142 kB)
  Using cached idna-3.4-py3-none-

In [ ]:
music_out = "output.wav"
x, fs = sf.read(music_out)
x2 = x.copy()

tiempo_inicial =  25# @param
tiempo_final =  35# @param
frecuencia_de_corte1= 1000 # @param
frecuencia_de_corte2= 5000 # @param

ti = tiempo_inicial
tf = tiempo_final
xs = x2[int(ti*fs):int((tf*fs)),:]
K= int(len(xs)/2) + 1
print(f'Audion Original')
Audio([xs[:,1], xs[:,0]],rate=fs) #segmento de audio

Audion Original


In [ ]:
#@markdown * Para filtrado paso alto utilizar: highpass
#@markdown * Para filtrado paso bajo utilizar: lowpass
#@markdown * Para filtrado pasabada utilizar: bandpass
#@markdown * Para filtrado rechazabanda utilizar:bandstop
filtro = "bandpass" #@param {type:'string'}
orden = 6 #@param
if filtro == 'highpass' or filtro =='lowpass':
  Wn=frecuencia_de_corte1
elif filtro == 'bandpass' or filtro=='bandstop':
  Wn=[frecuencia_de_corte1,frecuencia_de_corte2]
N = orden
num, den = butter(N,Wn=Wn,btype= filtro, output='ba',fs=fs)

xf = filtfilt(num, den, xs, axis=0)
print('audio filtrado')
Audio([xf[:,1], xf[:,0]],rate=fs) #Resultado

audio filtrado


In [ ]:
N = orden


# Diseñar el filtro Chebyshev tipo I
num, den = cheby1(N, rp, Wn=Wn, btype=filtro, analog=False, output='ba', fs=fs)

# Filtrar la señal
xf = filtfilt(num, den, xs, axis=0)

# Imprimir mensaje y mostrar el resultado
print('Audio filtrado')
Audio([xf[:, 1], xf[:, 0]], rate=fs)

# Graficar la respuesta en frecuencia del filtro
w, h = freqz(num, den, fs=fs)
plt.figure(figsize=(10, 6))
plt.plot(0.5 * fs * w / np.pi, 20 * np.log10(np.abs(h)), 'b')
plt.title('Respuesta en Frecuencia del Filtro Chebyshev Type I')
plt.xlabel('Frecuencia (Hz)')
plt.ylabel('Ganancia (dB)')
plt.grid()
plt.show()

NameError: ignored

In [ ]:
from scipy.signal import cheby2, filtfilt, freqz
import matplotlib.pyplot as plt
from IPython.display import Audio

# Parámetros del filtro
filtro = "bandstop"  #@param {type:'string'}
orden = 6
rp = 10  # Parámetro de la máxima ondulación permitida en la banda de paso

# Definir las frecuencias de corte según el tipo de filtro
frecuencia_de_corte1= 1000 # @param
frecuencia_de_corte2= 20000 # @param
if filtro == 'highpass' or filtro == 'lowpass':
    Wn = frecuencia_de_corte1
elif filtro == 'bandpass' or filtro == 'bandstop':
    Wn = [frecuencia_de_corte1, frecuencia_de_corte2]

N = orden

# Diseñar el filtro Chebyshev tipo II
num, den = cheby2(N, rp, Wn=Wn, btype=filtro, analog=False, output='ba', fs=fs)

# Filtrar la señal
xf = filtfilt(num, den, xs, axis=0)

# Imprimir mensaje y mostrar el resultado
print('Audio filtrado')
Audio([xf[:, 1], xf[:, 0]], rate=fs)

# Graficar la respuesta en frecuencia del filtro
w, h = freqz(num, den, fs=fs)
plt.figure(figsize=(10, 6))
plt.plot(0.5 * fs * w / np.pi, 20 * np.log10(np.abs(h)), 'b')
plt.title('Respuesta en Frecuencia del Filtro Chebyshev Type II')
plt.xlabel('Frecuencia (Hz)')
plt.ylabel('Ganancia (dB)')
plt.grid()
plt.show()

In [ ]:
from scipy.signal import bessel, filtfilt, freqz
import matplotlib.pyplot as plt
from IPython.display import Audio

# Parámetros del filtro
filtro = "highpass"  #@param {type:'string'}
orden = 6
# Definir las frecuencias de corte según el tipo de filtro
frecuencia_de_corte1= 5000 # @param
frecuencia_de_corte2= 20000 # @param
if filtro == 'highpass' or filtro == 'lowpass':
    Wn = frecuencia_de_corte1
elif filtro == 'bandpass' or filtro == 'bandstop':
    Wn = [frecuencia_de_corte1, frecuencia_de_corte2]

N = orden
normalization = 'mag' #Ajusta la frecuencia crítica según la respuesta que se desea
# Diseñar el filtro Bessel
num, den = bessel(N, Wn=Wn, btype=filtro, norm=normalization, output='ba', fs=fs)

# Filtrar la señal
xf = filtfilt(num, den, xs, axis=0)

# Imprimir mensaje y mostrar el resultado
print('Audio filtrado')
Audio([xf[:, 1], xf[:, 0]], rate=fs)

# Graficar la respuesta en frecuencia del filtro
w, h = freqz(num, den, fs=fs)
plt.figure(figsize=(10, 6))
plt.plot(0.5 * fs * w / np.pi, 20 * np.log10(np.abs(h)), 'b')
plt.title('Respuesta en Frecuencia del Filtro Bessel')
plt.xlabel('Frecuencia (Hz)')
plt.ylabel('Ganancia (dB)')
plt.grid()
plt.show()

In [ ]:
from scipy.signal import ellip, filtfilt, freqz
import matplotlib.pyplot as plt
from IPython.display import Audio

# Parámetros del filtro
filtro = "bandstop"  #@param {type:'string'}
orden = 6 #@param
rp = 1  # Parámetro de la máxima ondulación permitida en la banda de paso
rs = 60  # Parámetro de la mínima atenuación en la banda de rechazo

# Definir las frecuencias de corte según el tipo de filtro
frecuencia_de_corte1= 1000 # @param
frecuencia_de_corte2= 20000 # @param
if filtro == 'highpass' or filtro == 'lowpass':
    Wn = frecuencia_de_corte1
elif filtro == 'bandpass' or filtro == 'bandstop':
    Wn = [frecuencia_de_corte1, frecuencia_de_corte2]

N = orden

# Diseñar el filtro elíptico
num, den = ellip(N, rp, rs, Wn=Wn, btype=filtro, analog=False, output='ba', fs=fs)

# Filtrar la señal
xf = filtfilt(num, den, xs, axis=0)

# Imprimir mensaje y mostrar el resultado
print('Audio filtrado')
Audio([xf[:, 1], xf[:, 0]], rate=fs)

# Graficar la respuesta en frecuencia del filtro
w, h = freqz(num, den, fs=fs)
plt.figure(figsize=(10, 6))
plt.plot(0.5 * fs * w / np.pi, 20 * np.log10(np.abs(h)), 'b')
plt.title('Respuesta en Frecuencia del Filtro Elíptico')
plt.xlabel('Frecuencia (Hz)')
plt.ylabel('Ganancia (dB)')
plt.grid()
plt.show()